<a href="https://colab.research.google.com/github/ankitpb/FakeNewsClassification/blob/main/Fake_news_Classifier_Dataset_Creation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#Description: This programs scrapes FAKE and REAL news data from a website

In [ ]:
#Import the dependencies
from bs4 import BeautifulSoup
import pandas as pd
import requests
import urllib.request
import time
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
from matplotlib import rcParams
plt.rcParams['figure.figsize'] = [10,10]
import seaborn as sns
sns.set_theme(style="darkgrid")

from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import precision_score, recall_score, f1_score, accuracy_score
from sklearn.model_selection import GridSearchCV

import tensorflow as tf
import tensorflow.keras as keras
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import Embedding
from keras.layers import Flatten



import nltk
from nltk import sent_tokenize
''' Required for Google Colab'''
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('stopwords')
''' Required for Google Colab'''
from nltk.corpus import stopwords
import nltk
nltk.download('stopwords')
from nltk.tokenize import word_tokenize
import nltk
nltk.download('punkt')


import re
import itertools
import datetime
import time
from collections import Counter
import string

import warnings
warnings.filterwarnings('ignore')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [ ]:
#Create lists to store the scraped data
authors = []
dates = []
statements = []
sources = []
targets = []

In [ ]:
#Create a function to scrape the site
def scrape_website(page_number):
  page_num = str(page_number) #Convert the page number to a string
  URL = 'https://www.politifact.com/factchecks/list/?page='+page_num #append the page number to complete the URL
  webpage = requests.get(URL)  #Make a request to the website
  #time.sleep(3)
  soup = BeautifulSoup(webpage.text, "html.parser") #Parse the text from the website
  #Get the tags and it's class
  statement_footer =  soup.find_all('footer',attrs={'class':'m-statement__footer'})  #Get the tag and it's class
  statement_quote = soup.find_all('div', attrs={'class':'m-statement__quote'}) #Get the tag and it's class
  statement_meta = soup.find_all('div', attrs={'class':'m-statement__meta'})#Get the tag and it's class
  target = soup.find_all('div', attrs={'class':'m-statement__meter'}) #Get the tag and it's class
  #loop through the footer class m-statement__footer to get the date and author
  for i in statement_footer:
    link1 = i.text.strip()
    name_and_date = link1.split()
    first_name = name_and_date[1]
    last_name = name_and_date[2]
    full_name = first_name+' '+last_name
    month = name_and_date[4]
    day = name_and_date[5]
    year = name_and_date[6]
    date = month+' '+day+' '+year
    dates.append(date)
    authors.append(full_name)
  #Loop through the div m-statement__quote to get the link
  for i in statement_quote:
    link2 = i.find_all('a')
    statements.append(link2[0].text.strip())
 #Loop through the div m-statement__meta to get the source
  for i in statement_meta:
    link3 = i.find_all('a') #Source
    source_text = link3[0].text.strip()
    sources.append(source_text)
  #Loop through the target or the div m-statement__meter to get the facts about the statement (True or False)
  for i in target:
    fact = i.find('div', attrs={'class':'c-image'}).find('img').get('alt')
    targets.append(fact)

In [ ]:
#Loop through 'n-1' webpages to scrape the data
n=101
for i in range(1, n):
  scrape_website(i)

In [ ]:
#Create a new dataFrame 
data = pd.DataFrame(columns = ['author',  'statement', 'source', 'date', 'target']) 
data['author'] = authors
data['statement'] = statements
data['source'] = sources
data['date'] = dates
data['target'] = targets
#Show the data set
data

author  \
0               Yacob Reyes   
1        Samantha Putterman   
2          Analisa Trofimuk   
3              Jill Terreri   
4             Madeline Heim   
5             Tom Kertscher   
6        Samantha Putterman   
7        Samantha Putterman   
8         Gabrielle Settles   
9             Tom Kertscher   
10              Andy Nguyen   
11             Jeff Cercone   
12            Monique Curet   
13            Monique Curet   
14           Ciara O'Rourke   
15           Ciara O'Rourke   
16            Laura Schulte   
17       Samantha Putterman   
18        Gabrielle Settles   
19           Ciara O'Rourke   
20              Yacob Reyes   
21             Jeff Cercone   
22           Ciara O'Rourke   
23           Madison Czopek   
24       Samantha Putterman   
25            Monique Curet   
26             Warren Fiske   
27            Tom Kertscher   
28            Monique Curet   
29              Yacob Reyes   
30        Gabrielle Settles   
31              Andy Nguyen   
32             Jeff Cercone   
33            Monique Curet   
34               D.L. Davis   
35           Ciara O'Rourke   
36       Samantha Putterman   
37            Tom Kertscher   
38            Madeline Heim   
39            Monique Curet   
40              Amy Sherman   
41             Jeff Cercone   
42            Monique Curet   
43               Sara Swann   
44        Gabrielle Settles   
45             Jeff Cercone   
46             Lauren White   
47           Ciara O'Rourke   
48            Bill McCarthy   
49            Monique Curet   
50            Monique Curet   
51            Monique Curet   
52            Jon Greenberg   
53              Tom Gaughan   
54            Jon Greenberg   
55       Samantha Putterman   
56            Tom Kertscher   
57           Madison Czopek   
58            Tom Kertscher   
59            Bill McCarthy   
60             Jeff Cercone   
61            Bill McCarthy   
62       Samantha Putterman   
63            Bill McCarthy   
64            Nusaiba Mizan   
65           Louis Jacobson   
66            Jon Greenberg   
67              Paul Specht   
68               Sara Swann   
69            Tom Kertscher   
70               D.L. Davis   
71             Jill Terreri   
72           Louis Jacobson   
73         Analisa Trofimuk   
74            Monique Curet   
75            Monique Curet   
76             Jeff Cercone   
77            Jon Greenberg   
78            Monique Curet   
79           Ciara O'Rourke   
80              Yacob Reyes   
81        Gabrielle Settles   
82      Eleanor Hildebrandt   
83            Monique Curet   
84       Samantha Putterman   
85              Paul Specht   
86              Yacob Reyes   
87           Elizabeth Egan   
88              Amy Sherman   
89             Jeff Cercone   
90               Sara Swann   
91        Gabrielle Settles   
92           Ciara O'Rourke   
93            Tom Kertscher   
94             Warren Fiske   
95           Ciara O'Rourke   
96           Ciara O'Rourke   
97           Ciara O'Rourke   
98           Ciara O'Rourke   
99            Laura Schulte   
100          Ciara O'Rourke   
101      Samantha Putterman   
102           Bill McCarthy   
103           Jon Greenberg   
104          Ciara O'Rourke   
105          Ciara O'Rourke   
106           Tom Kertscher   
107           Bill McCarthy   
108          Ciara O'Rourke   
109          Ciara O'Rourke   
110             Yacob Reyes   
111             Yacob Reyes   
112      Samantha Putterman   
113           Madeline Heim   
114          Ciara O'Rourke   
115          Madison Czopek   
116            Jeff Cercone   
117      Samantha Putterman   
118          Ciara O'Rourke   
119          Ciara O'Rourke   
120          Ciara O'Rourke   
121           Bill McCarthy   
122           Jon Greenberg   
123          Ciara O'Rourke   
124              Vivian Lam   
125      Samantha Putterman   
126            Jeff Cercone   
127           Tom Kertscher   
128           Tom Kert

In [ ]:
#Create a function to get a binary number from the target
def getBinaryNumTarget(text):
  if text == 'true':
    return 1
  else:
    return 0

In [ ]:
#Create a function to get only true or false values from the target
def getBinaryTarget(text):
  if text == 'true':
    return 'REAL'
  else:
    return 'FAKE'

In [ ]:
#Store the data in the dataframe
data['BinaryTarget'] = data['target'].apply(getBinaryTarget)
data['BinaryNumTarget'] = data['target'].apply(getBinaryNumTarget)

In [ ]:
data

author  \
0               Yacob Reyes   
1        Samantha Putterman   
2          Analisa Trofimuk   
3              Jill Terreri   
4             Madeline Heim   
5             Tom Kertscher   
6        Samantha Putterman   
7        Samantha Putterman   
8         Gabrielle Settles   
9             Tom Kertscher   
10              Andy Nguyen   
11             Jeff Cercone   
12            Monique Curet   
13            Monique Curet   
14           Ciara O'Rourke   
15           Ciara O'Rourke   
16            Laura Schulte   
17       Samantha Putterman   
18        Gabrielle Settles   
19           Ciara O'Rourke   
20              Yacob Reyes   
21             Jeff Cercone   
22           Ciara O'Rourke   
23           Madison Czopek   
24       Samantha Putterman   
25            Monique Curet   
26             Warren Fiske   
27            Tom Kertscher   
28            Monique Curet   
29              Yacob Reyes   
30        Gabrielle Settles   
31              Andy Nguyen   
32             Jeff Cercone   
33            Monique Curet   
34               D.L. Davis   
35           Ciara O'Rourke   
36       Samantha Putterman   
37            Tom Kertscher   
38            Madeline Heim   
39            Monique Curet   
40              Amy Sherman   
41             Jeff Cercone   
42            Monique Curet   
43               Sara Swann   
44        Gabrielle Settles   
45             Jeff Cercone   
46             Lauren White   
47           Ciara O'Rourke   
48            Bill McCarthy   
49            Monique Curet   
50            Monique Curet   
51            Monique Curet   
52            Jon Greenberg   
53              Tom Gaughan   
54            Jon Greenberg   
55       Samantha Putterman   
56            Tom Kertscher   
57           Madison Czopek   
58            Tom Kertscher   
59            Bill McCarthy   
60             Jeff Cercone   
61            Bill McCarthy   
62       Samantha Putterman   
63            Bill McCarthy   
64            Nusaiba Mizan   
65           Louis Jacobson   
66            Jon Greenberg   
67              Paul Specht   
68               Sara Swann   
69            Tom Kertscher   
70               D.L. Davis   
71             Jill Terreri   
72           Louis Jacobson   
73         Analisa Trofimuk   
74            Monique Curet   
75            Monique Curet   
76             Jeff Cercone   
77            Jon Greenberg   
78            Monique Curet   
79           Ciara O'Rourke   
80              Yacob Reyes   
81        Gabrielle Settles   
82      Eleanor Hildebrandt   
83            Monique Curet   
84       Samantha Putterman   
85              Paul Specht   
86              Yacob Reyes   
87           Elizabeth Egan   
88              Amy Sherman   
89             Jeff Cercone   
90               Sara Swann   
91        Gabrielle Settles   
92           Ciara O'Rourke   
93            Tom Kertscher   
94             Warren Fiske   
95           Ciara O'Rourke   
96           Ciara O'Rourke   
97           Ciara O'Rourke   
98           Ciara O'Rourke   
99            Laura Schulte   
100          Ciara O'Rourke   
101      Samantha Putterman   
102           Bill McCarthy   
103           Jon Greenberg   
104          Ciara O'Rourke   
105          Ciara O'Rourke   
106           Tom Kertscher   
107           Bill McCarthy   
108          Ciara O'Rourke   
109          Ciara O'Rourke   
110             Yacob Reyes   
111             Yacob Reyes   
112      Samantha Putterman   
113           Madeline Heim   
114          Ciara O'Rourke   
115          Madison Czopek   
116            Jeff Cercone   
117      Samantha Putterman   
118          Ciara O'Rourke   
119          Ciara O'Rourke   
120          Ciara O'Rourke   
121           Bill McCarthy   
122           Jon Greenberg   
123          Ciara O'Rourke   
124              Vivian Lam   
125      Samantha Putterman   
126            Jeff Cercone   
127           Tom Kertscher   
128           Tom Kert

In [ ]:
#Store the data to a CSV file
data.to_csv('political_fact_checker.csv')

In [ ]:
import os
import numpy as np 
import pandas as pd 
import warnings
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
warnings.filterwarnings("ignore")
pd.set_option("display.max_rows",None)
from sklearn import preprocessing
import matplotlib 
matplotlib.style.use('ggplot')
from sklearn.preprocessing import LabelEncoder

In [ ]:
df=pd.read_csv("/content/political_fact_checker.csv")
df.head()

Unnamed: 0              author  \
0           0         Yacob Reyes   
1           1  Samantha Putterman   
2           2    Analisa Trofimuk   
3           3        Jill Terreri   
4           4       Madeline Heim   

                                           statement                  source  \
0  “Disney lost 172,000 reservations recently, va...          Facebook posts   
1  “Leftist justice reform” is the reason that th...          Facebook posts   
2  The Biden Administration is engaging in extrem...             Mary Miller   
3  “Cities in notoriously ‘tough on crime’ states...  Crystal Peoples-Stokes   
4  "Ron Johnson is trying to let insurance compan...         Sarah Godlewski   

             date       target BinaryTarget  BinaryNumTarget  
0  April 18, 2022        false         FAKE                0  
1  April 18, 2022        false         FAKE                0  
2  April 17, 2022        false         FAKE                0  
3     • April 16,    half-true         FAKE                0  
4  April 15, 2022  barely-true         FAKE                0

In [ ]:
df.dtypes

Unnamed: 0          int64
author             object
statement          object
source             object
date               object
target             object
BinaryTarget       object
BinaryNumTarget     int64
dtype: object

In [ ]:
string_col = df.select_dtypes(include="object").columns
df[string_col]=df[string_col].astype("string")

In [ ]:
df.dtypes

Unnamed: 0          int64
author             string
statement          string
source             string
date               string
target             string
BinaryTarget       string
BinaryNumTarget     int64
dtype: object

Exploratory Data Analysis

In [ ]:
# Shows the Distribution of Heat Diseases with respect to male and female
fig=px.histogram(df, 
                 x="BinaryNumTarget",
                 color="BinaryNumTarget",
                 hover_data=df.columns,
                 title="Distribution of Fake or Real",
                 barmode="group")
fig.show()

In [ ]:
df['BinaryNumTarget'].value_counts()

0    2892
1     108
Name: BinaryNumTarget, dtype: int64

Data Preprocessing


In [ ]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3000 entries, 0 to 2999
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Unnamed: 0       3000 non-null   int64 
 1   author           3000 non-null   string
 2   statement        3000 non-null   string
 3   source           3000 non-null   string
 4   date             3000 non-null   string
 5   target           3000 non-null   string
 6   BinaryTarget     3000 non-null   string
 7   BinaryNumTarget  3000 non-null   int64 
dtypes: int64(2), string(6)
memory usage: 187.6 KB


In [ ]:
df.isnull().sum()

Unnamed: 0         0
author             0
statement          0
source             0
date               0
target             0
BinaryTarget       0
BinaryNumTarget    0
dtype: int64

In [ ]:
gen_news_authors = set(list(df[df['BinaryNumTarget']==0]['author'].unique()))
fake_news_authors = set(list(df[df['BinaryNumTarget']==1]['author'].unique()))
overlapped_authors = gen_news_authors.intersection(fake_news_authors)
print("Number of distinct authors with genuine articles:", len(gen_news_authors))
print("Number of distinct authors with fake articles:", len(fake_news_authors))
print("Number of distinct authors with both genuine and fake:", len(overlapped_authors))

Number of distinct authors with genuine articles: 110
Number of distinct authors with fake articles: 45
Number of distinct authors with both genuine and fake: 36


In [ ]:
gen_news_authors = set(list(df[df['BinaryNumTarget']==0]['source'].unique()))
fake_news_authors = set(list(df[df['BinaryNumTarget']==1]['source'].unique()))
overlapped_authors = gen_news_authors.intersection(fake_news_authors)
print("Number of distinct source with genuine articles:", len(gen_news_authors))
print("Number of distinct source with fake articles:", len(fake_news_authors))
print("Number of distinct source with both genuine and fake:", len(overlapped_authors))

Number of distinct source with genuine articles: 532
Number of distinct source with fake articles: 83
Number of distinct source with both genuine and fake: 48


In [ ]:
from sklearn.model_selection import train_test_split

train_df, test_df = train_test_split(df, test_size=0.2, random_state=25)

print(f"No. of training examples: {train_df.shape[0]}")
print(f"No. of testing examples: {test_df.shape[0]}")

No. of training examples: 2400
No. of testing examples: 600


Text Cleaning

---


1. Remove special characters
2.Remove special characters Expand contractions
3.Convert to lower-case
4.Word Tokenize
5.Remove Stopwords


In [ ]:
text_cols = ['author', 'statement', 'source']

In [ ]:
import contractions
import re

def preprocess_text(x):
  cleaned_text = re.sub(r'[^a-zA-Z\d\s\']+', '', x)
  word_list = []
  for each_word in cleaned_text.split(' '):
    try:
      word_list.append(contractions.fix(each_word).lower())
    except:
      print(x)
  return " ".join(word_list)

In [ ]:
for col in text_cols:
  print("Processing column: {}".format(col))
  train_df[col] = train_df[col].apply(lambda x: preprocess_text(x))
  test_df[col] = test_df[col].apply(lambda x: preprocess_text(x)) 

Processing column: author


TypeError: ignored

In [ ]:
for col in text_cols:
  print("Processing column: {}".format(col))
  train_df[col] = train_df[col].apply(word_tokenize)
  test_df[col] = test_df[col].apply(word_tokenize)

Processing column: author
Processing column: statement
Processing column: source


In [ ]:
stoplist = set(stopwords.words("english"))
for col in text_cols:
  print("Processing column: {}".format(col))
  train_df[col] = train_df[col].apply(lambda x: [each_word for each_word in x if each_word not in stoplist])
  test_df[col] = test_df[col].apply(lambda x: [each_word for each_word in x if each_word not in stoplist])

Processing column: author
Processing column: statement
Processing column: source


In [ ]:
test_df.head() 

Unnamed: 0                author  \
1389        1389  [gabrielle, settles]   
987          987     [ciara, o'rourke]   
1017        1017        [amy, sherman]   
1245        1245        [kelsey, sena]   
1347        1347        [andy, nguyen]   

                                              statement              source  \
1389  [dandelion, root, able, kill, 98, cancer, cell...  [instagram, posts]   
987   [cdc, county, health, officials, obtained, 202...          [bloggers]   
1017  [stunning, report, nearly, 15, million, mailin...   [facebook, posts]   
1245          [americans, vaccinated, 2022, put, camps]  [instagram, posts]   
1347  [japan, banned, black, lives, matter, apparel,...   [facebook, posts]   

                    date       target BinaryTarget  BinaryNumTarget  
1389       June 17, 2021  barely-true         FAKE                0  
987   September 21, 2021   pants-fire         FAKE                0  
1017  September 14, 2021  barely-true         FAKE                0  
1245          • July 22,   pants-fire         FAKE                0  
1347       June 28, 2021    half-true         FAKE                0

In [ ]:
train_df['text_joined'] = train_df['statement'].apply(lambda x: " ".join(x))
test_df['text_joined'] = test_df['statement'].apply(lambda x: " ".join(x))

target = train_df['BinaryNumTarget'].values

count_vectorizer = CountVectorizer(ngram_range=(1, 2))
tf_idf_transformer = TfidfTransformer(smooth_idf=False)

# fit and transform train data to count vectorizer
count_vectorizer.fit(train_df['text_joined'].values)
count_vect_train = count_vectorizer.transform(train_df['text_joined'].values)

# fit the counts vector to tfidf transformer
tf_idf_transformer.fit(count_vect_train)
tf_idf_train = tf_idf_transformer.transform(count_vect_train)

# Transform the test data as well
count_vect_test = count_vectorizer.transform(test_df['text_joined'].values)
tf_idf_test = tf_idf_transformer.transform(count_vect_test)

Train test split

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(tf_idf_train, target, random_state=0)
df_perf_metrics = pd.DataFrame(columns=['Model', 'Accuracy_Training_Set', 'Accuracy_Test_Set', 'Precision', 'Recall', 'f1_score'])

In [ ]:
df_perf_metrics = pd.DataFrame(columns=[
    'Model', 'Accuracy_Training_Set', 'Accuracy_Test_Set', 'Precision',
    'Recall', 'f1_score', 'Training Time (secs'
])
models_trained_list = []


def get_perf_metrics(model, i):
    # model name
    model_name = type(model).__name__
    # time keeping
    start_time = time.time()
    print("Training {} model...".format(model_name))
    # Fitting of model
    model.fit(X_train, y_train)
    print("Completed {} model training.".format(model_name))
    elapsed_time = time.time() - start_time
    # Time Elapsed
    print("Time elapsed: {:.2f} s.".format(elapsed_time))
    # Predictions
    y_pred = model.predict(X_test)
    # Add to ith row of dataframe - metrics
    df_perf_metrics.loc[i] = [
        model_name,
        model.score(X_train, y_train),
        model.score(X_test, y_test),
        precision_score(y_test, y_pred),
        recall_score(y_test, y_pred),
        f1_score(y_test, y_pred), "{:.2f}".format(elapsed_time)
    ]
    # keep a track of trained models
    models_trained_list.append(model)
    print("Completed {} model's performance assessment.".format(model_name))

In [ ]:
models_list = [LogisticRegression(),
               MultinomialNB(),
               RandomForestClassifier(),
               DecisionTreeClassifier(),
               GradientBoostingClassifier(),
               AdaBoostClassifier()]

In [ ]:
for n, model in enumerate(models_list):
    get_perf_metrics(model, n)

Training LogisticRegression model...
Completed LogisticRegression model training.
Time elapsed: 0.14 s.
Completed LogisticRegression model's performance assessment.
Training MultinomialNB model...
Completed MultinomialNB model training.
Time elapsed: 0.01 s.
Completed MultinomialNB model's performance assessment.
Training RandomForestClassifier model...
Completed RandomForestClassifier model training.
Time elapsed: 1.63 s.
Completed RandomForestClassifier model's performance assessment.
Training DecisionTreeClassifier model...
Completed DecisionTreeClassifier model training.
Time elapsed: 0.27 s.
Completed DecisionTreeClassifier model's performance assessment.
Training GradientBoostingClassifier model...
Completed GradientBoostingClassifier model training.
Time elapsed: 5.12 s.
Completed GradientBoostingClassifier model's performance assessment.
Training AdaBoostClassifier model...
Completed AdaBoostClassifier model training.
Time elapsed: 2.21 s.
Completed AdaBoostClassifier model's p

In [ ]:
df_perf_metrics

Model  Accuracy_Training_Set  Accuracy_Test_Set  \
0          LogisticRegression               0.967778           0.965000   
1               MultinomialNB               0.967778           0.965000   
2      RandomForestClassifier               1.000000           0.965000   
3      DecisionTreeClassifier               1.000000           0.950000   
4  GradientBoostingClassifier               1.000000           0.956667   
5          AdaBoostClassifier               0.983889           0.955000   

   Precision  Recall  f1_score Training Time (secs  
0        0.0     0.0       0.0                0.14  
1        0.0     0.0       0.0                0.01  
2        0.0     0.0       0.0                1.63  
3        0.0     0.0       0.0                0.27  
4        0.0     0.0       0.0                5.12  
5        0.0     0.0       0.0                2.21

In [ ]:
train_df['all_info'] = train_df['author'] + train_df['statement'] + train_df['source']
test_df['all_info'] = test_df['author'] + test_df['statement'] + test_df['source']

In [ ]:
tokenizer = Tokenizer(oov_token = "<OOV>", num_words=6000)
tokenizer.fit_on_texts(train_df['all_info'])

In [ ]:
target = train_df['BinaryNumTarget'].values

In [ ]:
max_length = 40
vocab_size = 6000

sequences_train = tokenizer.texts_to_sequences(train_df['all_info'])
sequences_test = tokenizer.texts_to_sequences(test_df['all_info'])

padded_train = pad_sequences(sequences_train, padding = 'post', maxlen=max_length)
padded_test = pad_sequences(sequences_test, padding = 'post', maxlen=max_length)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(padded_train, target, test_size=0.2)

In [ ]:
X_train.shape, y_train.shape

((1920, 40), (1920,))

In [ ]:
def get_simple_model():
    model = Sequential()
    model.add(Embedding(vocab_size, 10, input_length=max_length))
    model.add(Flatten())
    model.add(Dense(1, activation='sigmoid'))
    return model

In [ ]:
best_model_file_name = "models/best_model_simple.hdf5"
callbacks=[
    keras.callbacks.EarlyStopping(monitor="val_loss", patience=15, 
                                  verbose=1, mode="min", restore_best_weights=True),
    keras.callbacks.ModelCheckpoint(filepath=best_model_file_name, verbose=1, save_best_only=True)
]

In [ ]:
model = get_simple_model()
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 40, 10)            60000     
                                                                 
 flatten (Flatten)           (None, 400)               0         
                                                                 
 dense (Dense)               (None, 1)                 401       
                                                                 
Total params: 60,401
Trainable params: 60,401
Non-trainable params: 0
_________________________________________________________________


In [ ]:
model.compile(loss='binary_crossentropy',
              optimizer='adam', 
              metrics=[tf.keras.metrics.Precision(), tf.keras.metrics.Recall()])

In [ ]:
history = model.fit(X_train, 
                    y_train, 
                    epochs=20,
                    validation_data=(X_test, y_test), 
                    callbacks=callbacks)

Epoch 1/20
41/60 [===================>..........] - ETA: 0s - loss: 0.5978 - precision: 0.0208 - recall: 0.0667
Epoch 1: val_loss improved from inf to 0.29061, saving model to models/best_model_simple.hdf5
60/60 [==============================] - 2s 10ms/step - loss: 0.5251 - precision: 0.0208 - recall: 0.0476 - val_loss: 0.2906 - val_precision: 0.0000e+00 - val_recall: 0.0000e+00
Epoch 2/20
52/60 [=========================>....] - ETA: 0s - loss: 0.1836 - precision: 0.0000e+00 - recall: 0.0000e+00
Epoch 2: val_loss improved from 0.29061 to 0.14712, saving model to models/best_model_simple.hdf5
60/60 [==============================] - 0s 3ms/step - loss: 0.1805 - precision: 0.0000e+00 - recall: 0.0000e+00 - val_loss: 0.1471 - val_precision: 0.0000e+00 - val_recall: 0.0000e+00
Epoch 3/20
48/60 [=======================>......] - ETA: 0s - loss: 0.1439 - precision: 0.0000e+00 - recall: 0.0000e+00
Epoch 3: val_loss improved from 0.14712 to 0.14261, saving model to models/best_model_simple.

In [ ]:
model = keras.models.load_model(best_model_file_name)
y_pred = (model.predict(X_test) > 0.5).astype("int32")
print('Accuracy: ', accuracy_score(y_test, y_pred))
print('Precision: ', precision_score(y_test, y_pred))
print('Recall: ', recall_score(y_test, y_pred))
print('F1 Score: ', f1_score(y_test, y_pred))

Accuracy:  0.9666666666666667
Precision:  0.0
Recall:  0.0
F1 Score:  0.0


In [ ]:
X = df.drop('BinaryNumTarget',axis='columns')
y=df['BinaryNumTarget']
y.value_counts()

0    2892
1     108
Name: BinaryNumTarget, dtype: int64

### Upsampling


In [ ]:
count_class_0,count_class_1 = df.BinaryNumTarget.value_counts()

df_class_0 = df[df['BinaryNumTarget']==0]
df_class_1 = df[df['BinaryNumTarget']==1]

df_class_1_over = df_class_1.sample(count_class_0,replace=True) 
df_test_over = pd.concat([df_class_0,df_class_1_over],axis=0)
df_test_over.shape

(5784, 8)

In [ ]:
from sklearn.model_selection import train_test_split

train2_df, test2_df = train_test_split(df_test_over, test_size=0.2, random_state=25)

print(f"No. of training examples: {train2_df.shape[0]}")
print(f"No. of testing examples: {test2_df.shape[0]}")

No. of training examples: 4627
No. of testing examples: 1157


In [ ]:
text_cols = ['author', 'statement', 'source']

In [ ]:
import contractions
import re

def preprocess_text(x):
  cleaned_text = re.sub(r'[^a-zA-Z\d\s\']+', '', x)
  word_list = []
  for each_word in cleaned_text.split(' '):
    try:
      word_list.append(contractions.fix(each_word).lower())
    except:
      print(x)
  return " ".join(word_list)

In [ ]:
for col in text_cols:
  print("Processing column: {}".format(col))
  train2_df[col] = train2_df[col].apply(lambda x: preprocess_text(x))
  test2_df[col] = test2_df[col].apply(lambda x: preprocess_text(x)) 

Processing column: author
Processing column: statement
Processing column: source


In [ ]:
for col in text_cols:
  print("Processing column: {}".format(col))
  train2_df[col] = train2_df[col].apply(word_tokenize)
  test2_df[col] = test2_df[col].apply(word_tokenize)

Processing column: author
Processing column: statement
Processing column: source


In [ ]:
stoplist = set(stopwords.words("english"))
for col in text_cols:
  print("Processing column: {}".format(col))
  train2_df[col] = train2_df[col].apply(lambda x: [each_word for each_word in x if each_word not in stoplist])
  test2_df[col] = test2_df[col].apply(lambda x: [each_word for each_word in x if each_word not in stoplist])

Processing column: author
Processing column: statement
Processing column: source


In [ ]:
test2_df.head() 

Unnamed: 0              author  \
1928        1928  [victoria, knight]   
2072        2072    [madison, black]   
175          175     [jill, terreri]   
45            45     [jeff, cercone]   
2067        2067   [ciara, o'rourke]   

                                              statement              source  \
1928  [becerra, supports, bernies, government, takeo...       [tom, cotton]   
2072  [insulin, prices, gone, thru, roof, patientsta...   [chuck, grassley]   
175   [1, among, large, states, fully, vaccinated, t...     [kathy, hochul]   
45    [photo, injured, ukrainian, woman, 2018, russi...  [instagram, posts]   
2067         [myanmar, used, dominion, voting, systems]   [facebook, posts]   

                  date target BinaryTarget  BinaryNumTarget  
1928     March 1, 2021   true         REAL                1  
2072  February 2, 2021   true         REAL                1  
175        • March 11,   true         REAL                1  
45       April 7, 2022  false         FAKE                0  
2067  February 2, 2021  false         FAKE                0

In [ ]:
train2_df['text_joined'] = train2_df['statement'].apply(lambda x: " ".join(x))
test2_df['text_joined'] = test2_df['statement'].apply(lambda x: " ".join(x))

target = train2_df['BinaryNumTarget'].values

count_vectorizer = CountVectorizer(ngram_range=(1, 2))
tf_idf_transformer = TfidfTransformer(smooth_idf=False)

# fit and transform train data to count vectorizer
count_vectorizer.fit(train2_df['text_joined'].values)
count_vect_train = count_vectorizer.transform(train2_df['text_joined'].values)

# fit the counts vector to tfidf transformer
tf_idf_transformer.fit(count_vect_train)
tf_idf_train = tf_idf_transformer.transform(count_vect_train)

# Transform the test data as well
count_vect_test = count_vectorizer.transform(test2_df['text_joined'].values)
tf_idf_test = tf_idf_transformer.transform(count_vect_test)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(tf_idf_train, target, random_state=0)
df_perf_metrics = pd.DataFrame(columns=['Model', 'Accuracy_Training_Set', 'Accuracy_Test_Set', 'Precision', 'Recall', 'f1_score'])

In [ ]:
df_perf_metrics = pd.DataFrame(columns=[
    'Model', 'Accuracy_Training_Set', 'Accuracy_Test_Set', 'Precision',
    'Recall', 'f1_score', 'Training Time (secs'
])
models_trained_list = []


def get_perf_metrics(model, i):
    # model name
    model_name = type(model).__name__
    # time keeping
    start_time = time.time()
    print("Training {} model...".format(model_name))
    # Fitting of model
    model.fit(X_train, y_train)
    print("Completed {} model training.".format(model_name))
    elapsed_time = time.time() - start_time
    # Time Elapsed
    print("Time elapsed: {:.2f} s.".format(elapsed_time))
    # Predictions
    y_pred = model.predict(X_test)
    # Add to ith row of dataframe - metrics
    df_perf_metrics.loc[i] = [
        model_name,
        model.score(X_train, y_train),
        model.score(X_test, y_test),
        precision_score(y_test, y_pred),
        recall_score(y_test, y_pred),
        f1_score(y_test, y_pred), "{:.2f}".format(elapsed_time)
    ]
    # keep a track of trained models
    models_trained_list.append(model)
    print("Completed {} model's performance assessment.".format(model_name))

In [ ]:
models_list = [LogisticRegression(),
               MultinomialNB(),
               RandomForestClassifier(),
               DecisionTreeClassifier(),
               GradientBoostingClassifier(),
               AdaBoostClassifier()]

In [ ]:
for n, model in enumerate(models_list):
    get_perf_metrics(model, n)

Training LogisticRegression model...
Completed LogisticRegression model training.
Time elapsed: 0.29 s.
Completed LogisticRegression model's performance assessment.
Training MultinomialNB model...
Completed MultinomialNB model training.
Time elapsed: 0.01 s.
Completed MultinomialNB model's performance assessment.
Training RandomForestClassifier model...
Completed RandomForestClassifier model training.
Time elapsed: 3.36 s.
Completed RandomForestClassifier model's performance assessment.
Training DecisionTreeClassifier model...
Completed DecisionTreeClassifier model training.
Time elapsed: 0.29 s.
Completed DecisionTreeClassifier model's performance assessment.
Training GradientBoostingClassifier model...
Completed GradientBoostingClassifier model training.
Time elapsed: 9.29 s.
Completed GradientBoostingClassifier model's performance assessment.
Training AdaBoostClassifier model...
Completed AdaBoostClassifier model training.
Time elapsed: 8.09 s.
Completed AdaBoostClassifier model's p

In [ ]:
df_perf_metrics

Model  Accuracy_Training_Set  Accuracy_Test_Set  \
0          LogisticRegression               1.000000           0.999136   
1               MultinomialNB               0.988473           0.933449   
2      RandomForestClassifier               1.000000           1.000000   
3      DecisionTreeClassifier               1.000000           0.980121   
4  GradientBoostingClassifier               0.973487           0.956785   
5          AdaBoostClassifier               0.935447           0.935177   

   Precision    Recall  f1_score Training Time (secs  
0   0.998342  1.000000  0.999170                0.29  
1   0.886598  1.000000  0.939891                0.01  
2   1.000000  1.000000  1.000000                3.36  
3   0.963200  1.000000  0.981255                0.29  
4   0.960000  0.956811  0.958403                9.29  
5   0.948893  0.925249  0.936922                8.09

In [ ]:
train2_df['all_info'] = train2_df['author'] + train2_df['statement'] + train2_df['source']
test2_df['all_info'] = test2_df['author'] + test2_df['statement'] + test2_df['source']

In [ ]:
tokenizer = Tokenizer(oov_token = "<OOV>", num_words=6000)
tokenizer.fit_on_texts(train2_df['all_info'])

In [ ]:
target = train2_df['BinaryNumTarget'].values

In [ ]:
max_length = 40
vocab_size = 6000

sequences_train = tokenizer.texts_to_sequences(train2_df['all_info'])
sequences_test = tokenizer.texts_to_sequences(test2_df['all_info'])

padded_train = pad_sequences(sequences_train, padding = 'post', maxlen=max_length)
padded_test = pad_sequences(sequences_test, padding = 'post', maxlen=max_length)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(padded_train, target, test_size=0.2)

In [ ]:
X_train.shape, y_train.shape

((3701, 40), (3701,))

In [ ]:
def get_simple_model():
    model = Sequential()
    model.add(Embedding(vocab_size, 10, input_length=max_length))
    model.add(Flatten())
    model.add(Dense(1, activation='sigmoid'))
    return model

In [ ]:
best_model_file_name = "models/best_model_simple.hdf5"
callbacks=[
    keras.callbacks.EarlyStopping(monitor="val_loss", patience=15, 
                                  verbose=1, mode="min", restore_best_weights=True),
    keras.callbacks.ModelCheckpoint(filepath=best_model_file_name, verbose=1, save_best_only=True)
]

In [ ]:
model = get_simple_model()
model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_1 (Embedding)     (None, 40, 10)            60000     
                                                                 
 flatten_1 (Flatten)         (None, 400)               0         
                                                                 
 dense_1 (Dense)             (None, 1)                 401       
                                                                 
Total params: 60,401
Trainable params: 60,401
Non-trainable params: 0
_________________________________________________________________


In [ ]:
model.compile(loss='binary_crossentropy',
              optimizer='adam', 
              metrics=[tf.keras.metrics.Precision(), tf.keras.metrics.Recall()])

In [ ]:
history = model.fit(X_train, 
                    y_train, 
                    epochs=20,
                    validation_data=(X_test, y_test), 
                    callbacks=callbacks)

Epoch 1/20
110/116 [===========================>..] - ETA: 0s - loss: 0.6267 - precision_1: 0.8514 - recall_1: 0.8753
Epoch 1: val_loss improved from inf to 0.49785, saving model to models/best_model_simple.hdf5
116/116 [==============================] - 3s 10ms/step - loss: 0.6210 - precision_1: 0.8518 - recall_1: 0.8814 - val_loss: 0.4978 - val_precision_1: 0.8528 - val_recall_1: 0.9934
Epoch 2/20
113/116 [============================>.] - ETA: 0s - loss: 0.3385 - precision_1: 0.9282 - recall_1: 0.9945
Epoch 2: val_loss improved from 0.49785 to 0.22151, saving model to models/best_model_simple.hdf5
116/116 [==============================] - 1s 6ms/step - loss: 0.3352 - precision_1: 0.9291 - recall_1: 0.9947 - val_loss: 0.2215 - val_precision_1: 0.9476 - val_recall_1: 0.9934
Epoch 3/20
103/116 [=========================>....] - ETA: 0s - loss: 0.1447 - precision_1: 0.9841 - recall_1: 0.9988
Epoch 3: val_loss improved from 0.22151 to 0.10778, saving model to models/best_model_simple.hd

In [ ]:
model = keras.models.load_model(best_model_file_name)
y_pred = (model.predict(X_test) > 0.5).astype("int32")
print('Accuracy: ', accuracy_score(y_test, y_pred))
print('Precision: ', precision_score(y_test, y_pred))
print('Recall: ', recall_score(y_test, y_pred))
print('F1 Score: ', f1_score(y_test, y_pred))

Accuracy:  1.0
Precision:  1.0
Recall:  1.0
F1 Score:  1.0
